In [1]:
import pandas as pd
import numpy as np
from sklearn.preprocessing import StandardScaler

import plotly.graph_objects as go
import ipywidgets as widgets

from axisproj import optimal, objective, make_basis

In [2]:
%load_ext autoreload

# For retina displays
%config InlineBackend.figure_format ='retina'

In [19]:
def prepare(data, method, knn=12):
    if method == 'lpp':
        X = data.T
        obj = objective.LPPObjective(knn=12,sigma=0.3)
        labs = None
    elif method == 'lde':
        X = data[:, :-1].T
        labs = np.ravel(data[:,-1])
        obj = objective.LDEObjective(knn=12, labs=labs)
    elif method == 'pca':
        X = data.T
        obj = objective.PCAObjective()
        labs = None
    else:
        print(f'unknown method: {method}')
        return
    
    X = StandardScaler().fit_transform(X.T).T
    
    return X, obj, labs

### Show Linear Projections

In [12]:
def show_lp(lp, colors, colorscale='Viridis', showscale=True):
    print(f'*** Linear Projections [{len(lp)}]')
    for i, p in enumerate(lp):
        V = p['V']
        Y = X.T.dot(V)

        t1 = go.Scatter(x=Y[:,0], y=Y[:,1], mode="markers", 
                        marker=dict(size=5, color=colors,  colorscale=colorscale, showscale=showscale))
        f1 = go.FigureWidget(go.Figure(data=[t1]))   

        t2 = go.Bar(y=p['histogram'])
        f2 = go.FigureWidget(go.Figure(data=[t2]))   
        print(f'LP:{i}')
        display(widgets.HBox([f1, f2]))   

### Show Axis Aligned Projections

In [10]:
def show_ap(ap, dims, colors, colorscale='Viridis', showscale=True):
    print(f'*** Axis Aligned [{len(ap)}]')
    for a in ap:
        alpha =  a['alpha']
        V = make_basis(X.shape[0], alpha)
        Y = X.T.dot(V)
        t1 = go.Figure(data=[go.Scatter(x=Y[:,0], y=Y[:,1], mode="markers", 
                                        marker=dict(size=5, 
                                                    color=colors,  
                                                    colorscale=colorscale, 
                                                    showscale=showscale))],
                      layout=go.Layout(
                          xaxis_title=dims[alpha[0]], 
                          yaxis_title=dims[alpha[1]]
                      ))
        f1 = go.FigureWidget(t1)

        t2 = go.Figure(data=[go.Bar(y=a['histogram'])])
        f2 = go.FigureWidget(t2)
        print(f'LP:{a["LP"]} alpha:{alpha}')
        display(widgets.HBox([f1, f2]))   

In [14]:
def run(X, obj, **kwargs):
    lp, ap = optimal(X, obj, normalize=False)
    dims = kwargs.pop('dims', None)
    show_lp(lp, **kwargs)
    show_ap(ap, dims, **kwargs)

###  seawater

In [20]:
%%time
data = pd.read_csv(f'../data/seawater.csv')
knn = 12
method = 'lpp'
X, obj, labs = prepare(data.values, method)
run(X, obj, dims=list(data), colors = X[51,:])

*** Linear Projections [8]
LP:0


    'data': [{'marker': {'color': array([ 0.05874728,  0.01835546,  0.13953092, …

LP:1


    'data': [{'marker': {'color': array([ 0.05874728,  0.01835546,  0.13953092, …

LP:2


...

LP:[6] alpha:(30, 31)


    'data': [{'marker': {'color': array([ 0.05874728,  0.01835546,  0.13953092, …

LP:[7] alpha:(19, 20)


    'data': [{'marker': {'color': array([ 0.05874728,  0.01835546,  0.13953092, …

CPU times: user 21.7 s, sys: 5.64 s, total: 27.4 s
Wall time: 25.9 s


### wine

In [21]:
%%time
data = pd.read_csv(f'../data/wine.csv')
method = 'lde'
X, obj, labs = prepare(data.values, method)
run(X, obj, 
    dims=list(data), 
    colors = (labs-1)/2,
    colorscale = [[0, 'red'], [0.5, 'blue'], [1, 'green']], 
    showscale=False)

*** Linear Projections [2]
LP:0


    'data': [{'marker': {'color': array([0. , 0. , 0. , 0. , 0. , 0. , 0. , 0. ,…

LP:1


    'data': [{'marker': {'color': array([0. , 0. , 0. , 0. , 0. , 0. , 0. , 0. ,…

*** Axis Aligned [2]
LP:[0] alpha:(9, 12)


    'data': [{'marker': {'color': array([0. , 0. , 0. , 0. , 0. , 0. , 0. , 0. ,…

LP:[1] alpha:(0, 12)


    'data': [{'marker': {'color': array([0. , 0. , 0. , 0. , 0. , 0. , 0. , 0. ,…

CPU times: user 3.3 s, sys: 88.5 ms, total: 3.38 s
Wall time: 3.88 s


### climate

In [ ]:
%%time
data = pd.read_csv(f'../data/climate.csv')
method = 'lde'
X, obj, labs = prepare(data.values, method)
run(X, obj, 
    dims=list(data), 
    colors = labs,
    colorscale = [[0, 'red'], [1, 'blue']],
    showscale=False)

*** Linear Projections [10]
LP:0


    'data': [{'marker': {'color': array([0., 1., 1., ..., 1., 1., 1.]),
        …

LP:1


    'data': [{'marker': {'color': array([0., 1., 1., ..., 1., 1., 1.]),
        …

LP:2


...

    'data': [{'marker': {'color': array([0., 1., 1., ..., 1., 1., 1.]),
        …

LP:9


    'data': [{'marker': {'color': array([0., 1., 1., ..., 1., 1., 1.]),
        …

*** Axis Aligned [2]
LP:[0, 1, 2, 4, 5, 6, 7, 8, 9] alpha:(1, 2)


    'data': [{'marker': {'color': array([0., 1., 1., ..., 1., 1., 1.]),
        …